In [1]:
from IPython.display import display
from matplotlib.ticker import StrMethodFormatter
from matplotlib.ticker import FormatStrFormatter

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
import spacy

pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.set_option('display.max_colwidth', None)

%matplotlib inline


In [2]:
#for text pre-processing
import re, string
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import SnowballStemmer
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
nltk.download('stopwords')
#for model-building
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report, f1_score, accuracy_score, confusion_matrix
from sklearn.metrics import roc_curve, auc, roc_auc_score
# bag of words
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
#for word embedding
import gensim
from gensim.models import Word2Vec

wl = WordNetLemmatizer()
snow = SnowballStemmer('english')


[nltk_data] Downloading package punkt to /home/mikes/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/mikes/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to /home/mikes/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /home/mikes/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
vd = pd.read_csv("/home/mikes/Windows/Documents/tmp/VAERS data deaths only Edited for NLP for HAD COVID.csv", 
                         delimiter = ",", 
                         encoding = "ISO-8859-1")

In [4]:
vd. columns

Index(['VAERS_ID', 'RECVDATE', 'STATE', 'AGE_YRS', 'CAGE_YR', 'CAGE_MO', 'SEX',
       'RPT_DATE', 'SYMPTOM_TEXT', 'SYMPTOM_TEXT_TARGET', 'DIED', 'DATEDIED',
       'L_THREAT', 'ER_VISIT', 'HOSPITAL', 'HOSPDAYS', 'X_STAY', 'DISABLE',
       'RECOVD', 'VAX_DATE', 'ONSET_DATE', 'NUMDAYS', 'LAB_DATA',
       'LAB_DATA_TARGET', 'V_ADMINBY', 'V_FUNDBY', 'OTHER_MEDS',
       'OTHER_MEDS_TARGET', 'CUR_ILL', 'CUR_ILL_TARGET', 'HISTORY',
       'PRIOR_VAX', 'SPLTTYPE', 'FORM_VERS', 'TODAYS_DATE', 'BIRTH_DEFECT',
       'OFC_VISIT', 'ER_ED_VISIT', 'ALLERGIES'],
      dtype='object')

In [6]:
#convert to lowercase and remove punctuations and characters and then strip
def preprocess(text):
    text = text.lower() #lowercase text
    text=text.strip()  #get rid of leading/trailing whitespace 
    text=re.compile('<.*?>').sub('', text) #Remove HTML tags/markups
    text = re.compile('[%s]' % re.escape(string.punctuation)).sub(' ', text)  #Replace punctuation with space. Careful since punctuation can sometime be useful
    text = re.sub('\s+', ' ', text)  #Remove extra space and tabs
    text = re.sub(r'\[[0-9]*\]',' ',text) #[0-9] matches any digit (0 to 10000...)
    text=re.sub(r'[^\w\s]', '', str(text).lower().strip())
    text = re.sub(r'\d',' ',text) #matches any digit from 0 to 100000..., \D matches non-digits
    text = re.sub(r'\s+',' ',text) #\s matches any whitespace, \s+ matches multiple whitespace, \S matches non-whitespace 
    
    return text

#1. STOPWORD REMOVAL
def stopword(string):
    a= [i for i in string.split() if i not in stopwords.words('english')]
    return ' '.join(a)

#2. STEMMING 
# Initialize the stemmer
#snow = SnowballStemmer('english')
def stemming(string):
    a=[snow.stem(i) for i in word_tokenize(string) ]
    return " ".join(a)

#3. LEMMATIZATION
# Initialize the lemmatizer
#wl = WordNetLemmatizer()
 
# This is a helper function to map NTLK position tags
# Full list is available here: https://www.ling.upenn.edu/courses/Fall_2003/ling001/penn_treebank_pos.html
def get_wordnet_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

# Tokenize the sentence
def lemmatizer(string):
    word_pos_tags = nltk.pos_tag(word_tokenize(string)) # Get position tags
    a=[wl.lemmatize(tag[0], get_wordnet_pos(tag[1])) for idx, tag in enumerate(word_pos_tags)] # Map the position tag and lemmatize the word/token
    return " ".join(a)

def finalpreprocess(string):
    string = str(string)
    return lemmatizer(stopword(preprocess(string)))
#    return lemmatizer(preprocess(string))

In [7]:
# if "apple" in stopwords.words('english'): print(1)

In [8]:
#for converting sentence to vectors/numbers from word vectors result by Word2Vec
class MeanEmbeddingVectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        # if a text is empty we should return a vector of zeros
        # with the same dimensionality as all the other vectors
        self.dim = len(next(iter(word2vec.values())))

    def fit(self, X, y):
        return self

    def transform(self, X):
        return np.array([
            np.mean([self.word2vec[w] for w in words if w in self.word2vec]
                    or [np.zeros(self.dim)], axis=0)
            for words in X
        ])

The precision is the ratio tp / (tp + fp) where tp is the number of true positives and fp the number of false positives. The precision is intuitively the ability of the classifier not to label as positive a sample that is negative.

The recall is the ratio tp / (tp + fn) where tp is the number of true positives and fn the number of false negatives. The recall is intuitively the ability of the classifier to find all the positive samples.

The F-beta score can be interpreted as a weighted harmonic mean of the precision and recall, where an F-beta score reaches its best value at 1 and worst score at 0.The F-beta score weights recall more than precision by a factor of beta. beta == 1.0 means recall and precision are equally important.

The support is the number of occurrences of each class in y_true.

If pos_label is None and in binary classification, this function returns the average precision, recall and F-measure if average is one of 'micro', 'macro', 'weighted' or 'samples'.

Read more in the [User Guide](https://scikit-learn.org/stable/modules/model_evaluation.html#precision-recall-f-measure-metrics).

In [9]:

def logistic_regression_tfidf(df_train, df_test, ID, TEXT, TARGET, perc_cutoff = 80):
    if perc_cutoff > 1: perc_cutoff = perc_cutoff/100
    df_train = df_train.loc[df_train[TARGET].notnull(), [ID, TEXT, TARGET ]]
    df_train['word_count'] = df_train[TEXT].apply(lambda x: len(str(x).split()))
    #print(df_train[df_train[TARGET]==1]['word_count'].mean()) #Positive match
    #print(df_train[df_train[TARGET]==0]['word_count'].mean()) #Not positive match 
    df_train['clean_text'] = df_train[TEXT].apply(lambda x: finalpreprocess(x))
    # create Word2vec model
    #  here words_f should be a list containing words from each document. say 1st row of the list is words from the 1st document/sentence
    #  length of words_f is number of documents/sentences in your dataset
    df_train['clean_text_tok']=[nltk.word_tokenize(i) for i in df_train['clean_text']] #convert preprocessed sentence to tokenized sentence
    model = Word2Vec(df_train['clean_text_tok'],min_count=1)  #min_count=1 means word should be present at least across all documents,
    #if min_count=2 means if the word is present less than 2 times across all the documents then we shouldn't consider it
    w2v = dict(zip(model.wv.index_to_key, model.wv.vectors))  #combination of word and its vector

    #SPLITTING THE TRAINING DATASET INTO TRAINING AND VALIDATION
    # Input: "reviewText", "rating" and "time"
    # Target: "log_votes"
    X_train, X_val, y_train, y_val = train_test_split(df_train["clean_text"],
                                                      df_train["SYMPTOM_TEXT_TARGET"],
                                                      test_size=0.2,
                                                      shuffle=True)
    X_train_tok= [nltk.word_tokenize(i) for i in X_train]  #for word2vec
    X_val_tok= [nltk.word_tokenize(i) for i in X_val]      #for word2vec
    #TF-IDF
    # Convert x_train to vector since model can only run on numbers and not words- Fit and transform
    tfidf_vectorizer = TfidfVectorizer(use_idf=True)
    X_train_vectors_tfidf = tfidf_vectorizer.fit_transform(X_train) #tfidf runs on non-tokenized sentences unlike word2vec
    # Only transform x_test (not fit and transform)
    X_val_vectors_tfidf = tfidf_vectorizer.transform(X_val) #Don't fit() your TfidfVectorizer to your test data: it will 
    #change the word-indexes & weights to match test data. Rather, fit on the training data, then use the same train-data-
    #fit model on the test data, to reflect the fact you're analyzing the test data only based on what was learned without 
    #it, and the have compatible

    ######################################################################
    
    #FITTING THE CLASSIFICATION MODEL using Logistic Regression(tf-idf)
    lr_tfidf=LogisticRegression(solver = 'liblinear', C=10, penalty = 'l2')
    lr_tfidf.fit(X_train_vectors_tfidf, y_train)  #model

    #Predict y value for test dataset
    y_predict = lr_tfidf.predict(X_val_vectors_tfidf)
    y_prob = lr_tfidf.predict_proba(X_val_vectors_tfidf)[:,1]


    print(classification_report(y_val,y_predict))
    print('Confusion Matrix:',confusion_matrix(y_val, y_predict))

    fpr, tpr, thresholds = roc_curve(y_val, y_prob)
    roc_auc = auc(fpr, tpr)
    print('AUC:', roc_auc)

    ### EXAMINE TEST SET WITH MODEL. This includes the data from training (both pos and neg targets) ###
    df_test['clean_text'] = vd['SYMPTOM_TEXT'].apply(lambda x: finalpreprocess(x)) #preprocess the data
    X_test=df_test['clean_text'] 
    X_vector=tfidf_vectorizer.transform(X_test) #converting X_test to vector
    y_predict = lr_tfidf.predict(X_vector)      #use the trained model on X_vector
    y_prob = lr_tfidf.predict_proba(X_vector)[:,1]
    df_test['predict_prob']= y_prob
    df_test['target']= y_predict
    # display(df_test[['VAERS_ID','SYMPTOM_TEXT','predict_prob','target']].head())
    # #final=df_test[['id','target']].reset_index(drop=True)
    # #final.to_csv('submission.csv')
    df_results = df_test[(
                            (df_test["target"] == 1) & 
                            (df_test["predict_prob"] >= perc_cutoff)
    )]
    num_found = df_results.shape[0]
    num_total = df_test.shape[0]
    print("{}/{} ({})".format(num_found, num_total, num_found/num_total))
    return num_found,df_results

df_train = vd.loc[vd['SYMPTOM_TEXT_TARGET'].notnull(), ['VAERS_ID','SYMPTOM_TEXT', 'SYMPTOM_TEXT_TARGET' ]]
df_train['word_count'] = df_train['SYMPTOM_TEXT'].apply(lambda x: len(str(x).split()))
print(df_train[df_train['SYMPTOM_TEXT_TARGET']==1]['word_count'].mean()) #Has covid
print(df_train[df_train['SYMPTOM_TEXT_TARGET']==0]['word_count'].mean()) #Does not have covid
num_found,df_results = logistic_regression_tfidf(df_train, vd, 'VAERS_ID', 'SYMPTOM_TEXT', 'SYMPTOM_TEXT_TARGET')
display(df_results)


100.20792079207921
104.03960396039604
              precision    recall  f1-score   support

         0.0       0.70      0.93      0.80        15
         1.0       0.95      0.77      0.85        26

    accuracy                           0.83        41
   macro avg       0.83      0.85      0.83        41
weighted avg       0.86      0.83      0.83        41

Confusion Matrix: [[14  1]
 [ 6 20]]
AUC: 0.935897435897436
204/5184 (0.03935185185185185%)


VAERS_ID   RECVDATE STATE  AGE_YRS  CAGE_YR  CAGE_MO SEX   RPT_DATE  \
1       917117   1/1/2021    AR     82.0     82.0      NaN   M        NaN   
2       917790   1/3/2021    AR     90.0     90.0      NaN   F        NaN   
3       917793   1/3/2021    AR     78.0     78.0      NaN   F        NaN   
16      920832   1/5/2021    NY    104.0    104.0      NaN   F        NaN   
45      928933   1/8/2021    IA     56.0     56.0      NaN   F        NaN   
59      956903   1/9/2021   NaN     86.0     85.0      NaN   M        NaN   
77      934966  1/11/2021    CA      NaN      NaN      NaN   F        NaN   
88      937127  1/12/2021    AR     91.0     91.0      NaN   M        NaN   
89      937152  1/12/2021    AR     91.0     91.0      NaN   F        NaN   
90      937186  1/12/2021    AR     87.0     87.0      NaN   F        NaN   
177     952713  1/18/2021    MO     64.0     64.0      NaN   M        NaN   
189     954251  1/18/2021   NaN     71.0     71.0      NaN   F        NaN   
203     956365  1/19/2021    CA     81.0     81.0      NaN   F        NaN   
269     963235  1/21/2021    TX     94.0     94.0      NaN   F        NaN   
295     966856  1/22/2021    KY     90.0     90.0      NaN   F        NaN   
309     973820  1/24/2021   NaN     74.0     73.0      NaN   M  1/22/2021   
319     970930  1/25/2021    NC     91.0     91.0      NaN   M        NaN   
334     972392  1/25/2021    IL     78.0     78.0      NaN   F        NaN   
351     974454  1/26/2021   NaN     78.0     78.0      NaN   F        NaN   
386     978529  1/27/2021    WV     88.0     88.0      NaN   F        NaN   
389     978873  1/27/2021    CA      NaN      NaN      NaN   U        NaN   
402     979796  1/27/2021    TX     74.0     74.0      NaN   M        NaN   
405     979841  1/27/2021    MT     64.0     64.0      NaN   M        NaN   
410     981945  1/27/2021   NaN     96.0     95.0      NaN   M        NaN   
423     982354  1/28/2021   NaN     91.0     91.0      NaN   M        NaN   
425     982417  1/28/2021    KS     89.0     89.0      NaN   F        NaN   
428     982517  1/28/2021   NaN     66.0     66.0      NaN   M        NaN   
435     983169  1/28/2021    KY     83.0     83.0      NaN   M        NaN   
436     983173  1/28/2021    KY     86.0     86.0      NaN   F        NaN   
437     983184  1/28/2021    KY     87.0     87.0      NaN   F        NaN   
438     983187  1/28/2021    KY     92.0     92.0      NaN   M        NaN   
439     983189  1/28/2021    KY     92.0     92.0      NaN   F        NaN   
440     983192  1/28/2021    KY     89.0     89.0      NaN   F        NaN   
441     983193  1/28/2021    KY     96.0     96.0      NaN   F        NaN   
449     985367  1/29/2021    KY     83.0     83.0      NaN   M        NaN   
451     985451  1/29/2021    KY    101.0    101.0      NaN   F        NaN   
460     986672  1/29/2021    AZ     77.0     77.0      NaN   M        NaN   
461     986773  1/29/2021    VA     67.0     67.0      NaN   M        NaN   
468     987301  1/29/2021    NC     87.0     87.0      NaN   F        NaN   
496     992063   2/1/2021    WI     80.0     80.0      NaN   M        NaN   
502     992238   2/1/2021    MI     70.0     70.0      NaN   M        NaN   
503     992342   2/1/2021    AL     77.0     77.0      NaN   M        NaN   
509     992734   2/1/2021    KY     86.0     86.0      NaN   F        NaN   
525     994678   2/2/2021    KY     80.0      NaN      NaN   F        NaN   
526     994778   2/2/2021    SC     97.0     97.0      NaN   F        NaN   
534     995460   2/2/2021    NH     85.0     85.0      NaN   M        NaN   
541     996086   2/2/2021    CA     55.0     55.0      NaN   M        NaN   
618    1005301   2/5/2021    KY     88.0     88.0      NaN   F        NaN   
627    1006220   2/5/2021    KY     93.0     93.0      NaN   M        NaN   
665    1011492   2/8/2021    NH     94.0     94.0      NaN   F        NaN   
668    1011677   2/8/2021    NH    101.0    101.0      NaN   F        NaN   
66

In [12]:
results = []
for i in range(0,10,1):
    df_train = vd.loc[vd['SYMPTOM_TEXT_TARGET'].notnull(), ['VAERS_ID','SYMPTOM_TEXT', 'SYMPTOM_TEXT_TARGET' ]]
    df_train['word_count'] = df_train['SYMPTOM_TEXT'].apply(lambda x: len(str(x).split()))
    print(df_train[df_train['SYMPTOM_TEXT_TARGET']==1]['word_count'].mean()) #Has covid
    print(df_train[df_train['SYMPTOM_TEXT_TARGET']==0]['word_count'].mean()) #Does not have covid
    num_found,df_results = logistic_regression_tfidf(df_train, vd, 'VAERS_ID', 'SYMPTOM_TEXT', 'SYMPTOM_TEXT_TARGET')
    results.append(num_found/5184)

for i in results:
    print("{}%".format(i*100))
    
print("Average: {}%".format( (sum(results)/len(results)) * 100))

100.20792079207921
104.03960396039604
              precision    recall  f1-score   support

         0.0       0.90      0.95      0.93        20
         1.0       0.95      0.90      0.93        21

    accuracy                           0.93        41
   macro avg       0.93      0.93      0.93        41
weighted avg       0.93      0.93      0.93        41

Confusion Matrix: [[19  1]
 [ 2 19]]
AUC: 0.9928571428571428
282/5184 (0.05439814814814815%)
100.20792079207921
104.03960396039604
              precision    recall  f1-score   support

         0.0       0.89      0.89      0.89        18
         1.0       0.91      0.91      0.91        23

    accuracy                           0.90        41
   macro avg       0.90      0.90      0.90        41
weighted avg       0.90      0.90      0.90        41

Confusion Matrix: [[16  2]
 [ 2 21]]
AUC: 0.9734299516908212
244/5184 (0.0470679012345679%)
100.20792079207921
104.03960396039604
              precision    recall  f1-score   s

In [23]:
df = df_results.sort_values(by=['predict_prob'])
display(df[["SYMPTOM_TEXT", "predict_prob", "target"]])
# 12 out of 233 from last run were incorrect
# Accepting a 5% error rate at 80% "predict_prob"

SYMPTOM_TEXT  \
1188                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               Emergency Room HPI: The patient is a 71 y.o. female with a PMH notable for COPD, hypertension and anxiety and depression who presented on 2/6/2021 for evaluation of shortness of breath. Patient presented to our emergency room yesterday morning from local nursing facility rehab nursing staff reported that she had had a increased shortness of breath for the last 3 

# Conclusions
An examination of VARS COVID data (regarding reports of death only,) segregated from the entire VAERS COVID dataset downloaded July 2021. Manually marked rows positive (diagnosed with or tested positive for covid within 30 days before shot, after shot, or marked died of covid) or negative (not diagnosed, or tested positive for, or died of covid) based on the text in "SYMPTOM_TEXT." 

Trained the dataset using Logistic Regression(tf-idf), and then ran the model against the entire death-only VAERS data, including the data from the training set (in order to capture the total of all patients who had, developed, or died of covid.)

### Out of 10 runs...
282 Had covid out of 5184 VAERS reports of deaths (0.05439814814814815%)
244/5184 (0.0470679012345679%)
264/5184 (0.05092592592592592%)
273/5184 (0.052662037037037035%)
275/5184 (0.05304783950617284%)
218/5184 (0.04205246913580247%)
299/5184 (0.05767746913580247%)
210/5184 (0.04050925925925926%)
204/5184 (0.03935185185185185%)
233/5184 (0.044945987654320986%)

### Averages:
**250.2** reports out of 5184 reports of deaths after vaccination involved patients who were diagnosed with covid within 30 days before vaccination, during or after vaccination, or were listed as dying from covid infections.

**4.826388888888889%** reports out of 5184 reports of deaths after vaccination involved patients who were diagnosed with covid within 30 days before vaccination, during or after vaccination, or were listed as dying from covid infections.


